# Алгоритмы интеллектуальной обработки больших объемов данных
## Семинар, учимся настраивать параметры бустинга


Разберем, например, xgboost:
https://xgboost.readthedocs.io/en/latest/parameter.html

https://xgboost.readthedocs.io/en/latest/python/python_api.html

Параметры можно разделить на группы. 



1) Общие параметры алгоритма, например, тип бустинга

2) Параметры обучения бустинга, например число итераций, learning rate

3) Параметры построения деревьев, например, глубина, минимальное число элементов в листе

4) Параметры стохастики, subsample, colsample

5) Регуляриазция, например, lambda


ПРАВИЛЬНОГО алгоритма для тюнинга нет, вот один из вариантов, которые часто используют на практике.

1) Возьмите дефолтное параметры. Поставьте нужные loss и eval функции.  Измените максимальное  число деревьев, чтобы было не долго делать эксперименты

2) Подберите для него alpha, чтобы алгоритм не переобучался

3) Подберите параметры сложности дерева, например,  глубину, мин число объектов в листах, мин значение для расщепления и тд

4) Подберите паарметры стохастики

5) Подберите регуляризацию

6) Уменьшите leraning rate и обучите максимальное число деревьев, чтобы не переобучалось

Давайте настроим параметры бустинга на нашем конкурсе!

In [1020]:
doc_to_title = {}
with open('/Users/egor/Desktop/Техносфера/MachineLearning/project/docs_titles.tsv') as f:
    for num_line, line in enumerate(f):
        if num_line == 0:
            continue
        data = line.strip().split('\t', 1)
        doc_id = int(data[0])
        if len(data) == 1:
            title = ''
        else:
            title = data[1]
        doc_to_title[doc_id] = title
print (len(doc_to_title))


28026


In [1021]:
import pandas as pd
train_data = pd.read_csv('/Users/egor/Desktop/Техносфера/MachineLearning/project/train_groups.csv')
traingroups_titledata = {}
for i in range(len(train_data)):
    new_doc = train_data.iloc[i]
    doc_group = new_doc['group_id']
    doc_id = new_doc['doc_id']
    target = new_doc['target']
    title = doc_to_title[doc_id]
    if doc_group not in traingroups_titledata:
        traingroups_titledata[doc_group] = []
    traingroups_titledata[doc_group].append((doc_id, title, target))

In [1022]:
import numpy as np
y_train = []
X_train = []
groups_train = []
for new_group in traingroups_titledata:
    docs = traingroups_titledata[new_group]
    for k, (doc_id, title, target_id) in enumerate(docs):
        y_train.append(target_id)
        groups_train.append(new_group)
        all_dist = []
        words = set(title.strip().split())
        for j in range(0, len(docs)):
            if k == j:
                continue
            doc_id_j, title_j, target_j = docs[j]
            words_j = set(title_j.strip().split())
            all_dist.append(len(words.intersection(words_j)))
        X_train.append(sorted(all_dist, reverse=True)[0:25]    )
X_train = np.array(X_train)
y_train = np.array(y_train)
groups_train = np.array(groups_train)
print (X_train.shape, y_train.shape, groups_train.shape)

(11690, 25) (11690,) (11690,)


In [1023]:
test_data = pd.read_csv('/Users/egor/Desktop/Техносфера/MachineLearning/project/test_groups.csv')
testgroups_titledata = {}
for i in range(len(test_data)):
    new_doc = test_data.iloc[i]
    doc_group = new_doc['group_id']
    doc_id = new_doc['doc_id']
    title = doc_to_title[doc_id]
    if doc_group not in testgroups_titledata:
        testgroups_titledata[doc_group] = []
    testgroups_titledata[doc_group].append((doc_id, title))

In [1024]:
X_test = []
groups_test = []
for new_group in testgroups_titledata:
    docs = testgroups_titledata[new_group]
    for k, (doc_id, title) in enumerate(docs):
        groups_test.append(new_group)
        all_dist = []
        words = set(title.strip().split())
        for j in range(0, len(docs)):
            if k == j:
                continue
            doc_id_j, title_j = docs[j]
            words_j = set(title_j.strip().split())
            all_dist.append(len(words.intersection(words_j)))
        X_test.append(sorted(all_dist, reverse=True)[0:25])
X_test = np.array(X_test)
groups_test = np.array(groups_test)
print(X_test.shape, groups_test.shape)

(16627, 25) (16627,)


In [1025]:
test_data
pair_ids = test_data['pair_id'].tolist()

Подберите размер батча для обучения. Линейная модель не должна учиться дольше нескольких минут. 

Не забывайте использовать скейлер!

In [1026]:
import catboost
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import cross_val_score
import json

In [1027]:
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.fit_transform(X_test)

In [1028]:
model = catboost.CatBoostClassifier(depth=3)

In [1029]:
model.fit(X_train, y_train)

Learning rate set to 0.029437
0:	learn: 0.6780883	total: 8.56ms	remaining: 8.55s
1:	learn: 0.6645999	total: 14.6ms	remaining: 7.27s
2:	learn: 0.6519413	total: 21.9ms	remaining: 7.26s
3:	learn: 0.6396523	total: 29.9ms	remaining: 7.43s
4:	learn: 0.6283534	total: 36.5ms	remaining: 7.26s
5:	learn: 0.6187489	total: 44.4ms	remaining: 7.36s
6:	learn: 0.6094782	total: 50.5ms	remaining: 7.16s
7:	learn: 0.6003134	total: 59ms	remaining: 7.32s
8:	learn: 0.5923706	total: 65.6ms	remaining: 7.23s
9:	learn: 0.5844217	total: 71.8ms	remaining: 7.1s
10:	learn: 0.5761925	total: 79.5ms	remaining: 7.15s
11:	learn: 0.5689702	total: 85.9ms	remaining: 7.07s
12:	learn: 0.5625286	total: 92.3ms	remaining: 7.01s
13:	learn: 0.5567143	total: 101ms	remaining: 7.12s
14:	learn: 0.5517551	total: 107ms	remaining: 7.05s
15:	learn: 0.5461646	total: 117ms	remaining: 7.22s
16:	learn: 0.5407989	total: 124ms	remaining: 7.17s
17:	learn: 0.5356455	total: 130ms	remaining: 7.1s
18:	learn: 0.5313654	total: 141ms	remaining: 7.29s
19

169:	learn: 0.4501098	total: 2.31s	remaining: 11.3s
170:	learn: 0.4500739	total: 2.34s	remaining: 11.3s
171:	learn: 0.4500029	total: 2.35s	remaining: 11.3s
172:	learn: 0.4499613	total: 2.37s	remaining: 11.3s
173:	learn: 0.4499066	total: 2.38s	remaining: 11.3s
174:	learn: 0.4498898	total: 2.4s	remaining: 11.3s
175:	learn: 0.4497799	total: 2.41s	remaining: 11.3s
176:	learn: 0.4497550	total: 2.42s	remaining: 11.3s
177:	learn: 0.4496956	total: 2.44s	remaining: 11.2s
178:	learn: 0.4496290	total: 2.44s	remaining: 11.2s
179:	learn: 0.4495676	total: 2.45s	remaining: 11.2s
180:	learn: 0.4495561	total: 2.46s	remaining: 11.1s
181:	learn: 0.4495313	total: 2.47s	remaining: 11.1s
182:	learn: 0.4494717	total: 2.48s	remaining: 11.1s
183:	learn: 0.4494462	total: 2.49s	remaining: 11s
184:	learn: 0.4493963	total: 2.5s	remaining: 11s
185:	learn: 0.4493297	total: 2.51s	remaining: 11s
186:	learn: 0.4492685	total: 2.52s	remaining: 11s
187:	learn: 0.4492432	total: 2.53s	remaining: 10.9s
188:	learn: 0.4492167	

330:	learn: 0.4444298	total: 4.59s	remaining: 9.28s
331:	learn: 0.4444003	total: 4.62s	remaining: 9.29s
332:	learn: 0.4443884	total: 4.64s	remaining: 9.29s
333:	learn: 0.4443598	total: 4.66s	remaining: 9.29s
334:	learn: 0.4443270	total: 4.7s	remaining: 9.33s
335:	learn: 0.4442544	total: 4.73s	remaining: 9.35s
336:	learn: 0.4442441	total: 4.75s	remaining: 9.34s
337:	learn: 0.4442071	total: 4.76s	remaining: 9.33s
338:	learn: 0.4441776	total: 4.79s	remaining: 9.33s
339:	learn: 0.4441676	total: 4.8s	remaining: 9.32s
340:	learn: 0.4441368	total: 4.81s	remaining: 9.3s
341:	learn: 0.4441032	total: 4.82s	remaining: 9.28s
342:	learn: 0.4440708	total: 4.83s	remaining: 9.25s
343:	learn: 0.4440468	total: 4.84s	remaining: 9.23s
344:	learn: 0.4440037	total: 4.85s	remaining: 9.21s
345:	learn: 0.4439710	total: 4.86s	remaining: 9.18s
346:	learn: 0.4439448	total: 4.87s	remaining: 9.17s
347:	learn: 0.4439147	total: 4.88s	remaining: 9.14s
348:	learn: 0.4438781	total: 4.89s	remaining: 9.13s
349:	learn: 0.4

506:	learn: 0.4394609	total: 7.07s	remaining: 6.88s
507:	learn: 0.4394534	total: 7.08s	remaining: 6.86s
508:	learn: 0.4394406	total: 7.09s	remaining: 6.84s
509:	learn: 0.4394321	total: 7.1s	remaining: 6.82s
510:	learn: 0.4394139	total: 7.11s	remaining: 6.8s
511:	learn: 0.4393939	total: 7.13s	remaining: 6.8s
512:	learn: 0.4393580	total: 7.15s	remaining: 6.79s
513:	learn: 0.4393525	total: 7.16s	remaining: 6.77s
514:	learn: 0.4393192	total: 7.18s	remaining: 6.76s
515:	learn: 0.4392976	total: 7.19s	remaining: 6.75s
516:	learn: 0.4392775	total: 7.21s	remaining: 6.74s
517:	learn: 0.4392565	total: 7.22s	remaining: 6.72s
518:	learn: 0.4392384	total: 7.23s	remaining: 6.7s
519:	learn: 0.4392071	total: 7.24s	remaining: 6.68s
520:	learn: 0.4391985	total: 7.25s	remaining: 6.66s
521:	learn: 0.4391892	total: 7.26s	remaining: 6.64s
522:	learn: 0.4391595	total: 7.27s	remaining: 6.63s
523:	learn: 0.4391333	total: 7.28s	remaining: 6.61s
524:	learn: 0.4391315	total: 7.29s	remaining: 6.6s
525:	learn: 0.439

666:	learn: 0.4365487	total: 9.61s	remaining: 4.8s
667:	learn: 0.4365301	total: 9.63s	remaining: 4.79s
668:	learn: 0.4365185	total: 9.64s	remaining: 4.77s
669:	learn: 0.4365010	total: 9.65s	remaining: 4.75s
670:	learn: 0.4364704	total: 9.66s	remaining: 4.74s
671:	learn: 0.4364564	total: 9.67s	remaining: 4.72s
672:	learn: 0.4364393	total: 9.68s	remaining: 4.7s
673:	learn: 0.4364255	total: 9.69s	remaining: 4.68s
674:	learn: 0.4364092	total: 9.7s	remaining: 4.67s
675:	learn: 0.4363883	total: 9.71s	remaining: 4.66s
676:	learn: 0.4363679	total: 9.73s	remaining: 4.64s
677:	learn: 0.4363593	total: 9.75s	remaining: 4.63s
678:	learn: 0.4363420	total: 9.76s	remaining: 4.61s
679:	learn: 0.4363376	total: 9.79s	remaining: 4.61s
680:	learn: 0.4363136	total: 9.8s	remaining: 4.59s
681:	learn: 0.4363052	total: 9.82s	remaining: 4.58s
682:	learn: 0.4362923	total: 9.83s	remaining: 4.56s
683:	learn: 0.4362749	total: 9.84s	remaining: 4.55s
684:	learn: 0.4362567	total: 9.85s	remaining: 4.53s
685:	learn: 0.43

836:	learn: 0.4341236	total: 11.9s	remaining: 2.32s
837:	learn: 0.4341138	total: 11.9s	remaining: 2.3s
838:	learn: 0.4341009	total: 11.9s	remaining: 2.29s
839:	learn: 0.4340802	total: 11.9s	remaining: 2.27s
840:	learn: 0.4340751	total: 11.9s	remaining: 2.26s
841:	learn: 0.4340351	total: 11.9s	remaining: 2.24s
842:	learn: 0.4340324	total: 12s	remaining: 2.23s
843:	learn: 0.4340234	total: 12s	remaining: 2.21s
844:	learn: 0.4340188	total: 12s	remaining: 2.2s
845:	learn: 0.4339899	total: 12s	remaining: 2.18s
846:	learn: 0.4339679	total: 12s	remaining: 2.17s
847:	learn: 0.4339645	total: 12s	remaining: 2.15s
848:	learn: 0.4339533	total: 12s	remaining: 2.13s
849:	learn: 0.4339507	total: 12s	remaining: 2.12s
850:	learn: 0.4339331	total: 12s	remaining: 2.1s
851:	learn: 0.4339231	total: 12s	remaining: 2.09s
852:	learn: 0.4339206	total: 12s	remaining: 2.08s
853:	learn: 0.4339176	total: 12.1s	remaining: 2.06s
854:	learn: 0.4339005	total: 12.1s	remaining: 2.05s
855:	learn: 0.4338926	total: 12.1s	re

995:	learn: 0.4322011	total: 13.8s	remaining: 55.3ms
996:	learn: 0.4321964	total: 13.8s	remaining: 41.5ms
997:	learn: 0.4321922	total: 13.8s	remaining: 27.6ms
998:	learn: 0.4321863	total: 13.8s	remaining: 13.8ms
999:	learn: 0.4321823	total: 13.8s	remaining: 0us


Задача: обучите на этих фичах (число фичей рассатриваем как гипераматр) бустинг, подберите параметры, засабмитьте на кагл. Побейте 0.62 паблик скор за сутки.  Удачи!

In [1030]:
np.random.seed(0)
depthes = (2, 3, 4, 5, 6, 7)
scores = []
for depth in depthes:
    model = catboost.CatBoostClassifier(depth=depth)
    scores.append(cross_val_score(model, X_train, y_train, cv=5, scoring='f1').mean())

Learning rate set to 0.026761
0:	learn: 0.6803538	total: 3.06ms	remaining: 3.06s
1:	learn: 0.6687874	total: 5.82ms	remaining: 2.9s
2:	learn: 0.6577943	total: 9.09ms	remaining: 3.02s
3:	learn: 0.6477455	total: 12.8ms	remaining: 3.19s
4:	learn: 0.6378795	total: 15.9ms	remaining: 3.17s
5:	learn: 0.6278326	total: 18.8ms	remaining: 3.12s
6:	learn: 0.6185186	total: 21.9ms	remaining: 3.1s
7:	learn: 0.6093563	total: 24.8ms	remaining: 3.08s
8:	learn: 0.6011544	total: 28.1ms	remaining: 3.1s
9:	learn: 0.5937269	total: 31.3ms	remaining: 3.1s
10:	learn: 0.5870510	total: 34.5ms	remaining: 3.1s
11:	learn: 0.5800142	total: 37.3ms	remaining: 3.07s
12:	learn: 0.5733573	total: 40.3ms	remaining: 3.06s
13:	learn: 0.5672990	total: 44.4ms	remaining: 3.13s
14:	learn: 0.5610661	total: 49.6ms	remaining: 3.26s
15:	learn: 0.5563898	total: 54.7ms	remaining: 3.36s
16:	learn: 0.5518648	total: 59.9ms	remaining: 3.46s
17:	learn: 0.5465645	total: 68.8ms	remaining: 3.75s
18:	learn: 0.5417453	total: 71.9ms	remaining: 3.7

173:	learn: 0.4487647	total: 659ms	remaining: 3.13s
174:	learn: 0.4487355	total: 664ms	remaining: 3.13s
175:	learn: 0.4487178	total: 667ms	remaining: 3.12s
176:	learn: 0.4486695	total: 670ms	remaining: 3.11s
177:	learn: 0.4486212	total: 673ms	remaining: 3.11s
178:	learn: 0.4485692	total: 677ms	remaining: 3.1s
179:	learn: 0.4485348	total: 680ms	remaining: 3.1s
180:	learn: 0.4484979	total: 683ms	remaining: 3.09s
181:	learn: 0.4484321	total: 686ms	remaining: 3.08s
182:	learn: 0.4483403	total: 689ms	remaining: 3.08s
183:	learn: 0.4483165	total: 692ms	remaining: 3.07s
184:	learn: 0.4482296	total: 695ms	remaining: 3.06s
185:	learn: 0.4481960	total: 699ms	remaining: 3.06s
186:	learn: 0.4481402	total: 702ms	remaining: 3.05s
187:	learn: 0.4480753	total: 705ms	remaining: 3.04s
188:	learn: 0.4480481	total: 708ms	remaining: 3.04s
189:	learn: 0.4480173	total: 712ms	remaining: 3.03s
190:	learn: 0.4479988	total: 715ms	remaining: 3.03s
191:	learn: 0.4479319	total: 718ms	remaining: 3.02s
192:	learn: 0.

353:	learn: 0.4429772	total: 1.35s	remaining: 2.47s
354:	learn: 0.4429394	total: 1.36s	remaining: 2.47s
355:	learn: 0.4429340	total: 1.36s	remaining: 2.47s
356:	learn: 0.4429267	total: 1.37s	remaining: 2.46s
357:	learn: 0.4429031	total: 1.37s	remaining: 2.46s
358:	learn: 0.4429028	total: 1.37s	remaining: 2.45s
359:	learn: 0.4428894	total: 1.38s	remaining: 2.45s
360:	learn: 0.4428699	total: 1.38s	remaining: 2.44s
361:	learn: 0.4428293	total: 1.38s	remaining: 2.44s
362:	learn: 0.4428122	total: 1.39s	remaining: 2.43s
363:	learn: 0.4427939	total: 1.39s	remaining: 2.43s
364:	learn: 0.4427679	total: 1.39s	remaining: 2.42s
365:	learn: 0.4427620	total: 1.4s	remaining: 2.42s
366:	learn: 0.4427366	total: 1.4s	remaining: 2.42s
367:	learn: 0.4427121	total: 1.4s	remaining: 2.41s
368:	learn: 0.4426892	total: 1.41s	remaining: 2.4s
369:	learn: 0.4426691	total: 1.41s	remaining: 2.4s
370:	learn: 0.4426480	total: 1.41s	remaining: 2.39s
371:	learn: 0.4426233	total: 1.42s	remaining: 2.39s
372:	learn: 0.442

520:	learn: 0.4397313	total: 1.93s	remaining: 1.78s
521:	learn: 0.4397195	total: 1.94s	remaining: 1.77s
522:	learn: 0.4396974	total: 1.94s	remaining: 1.77s
523:	learn: 0.4396853	total: 1.95s	remaining: 1.77s
524:	learn: 0.4396720	total: 1.95s	remaining: 1.76s
525:	learn: 0.4396566	total: 1.95s	remaining: 1.76s
526:	learn: 0.4396381	total: 1.96s	remaining: 1.75s
527:	learn: 0.4396301	total: 1.96s	remaining: 1.75s
528:	learn: 0.4396127	total: 1.96s	remaining: 1.75s
529:	learn: 0.4395843	total: 1.97s	remaining: 1.74s
530:	learn: 0.4395603	total: 1.97s	remaining: 1.74s
531:	learn: 0.4395496	total: 1.97s	remaining: 1.74s
532:	learn: 0.4395408	total: 1.98s	remaining: 1.73s
533:	learn: 0.4395231	total: 1.98s	remaining: 1.73s
534:	learn: 0.4395097	total: 1.98s	remaining: 1.72s
535:	learn: 0.4395068	total: 1.99s	remaining: 1.72s
536:	learn: 0.4394872	total: 1.99s	remaining: 1.72s
537:	learn: 0.4394765	total: 1.99s	remaining: 1.71s
538:	learn: 0.4394725	total: 2s	remaining: 1.71s
539:	learn: 0.4

690:	learn: 0.4374046	total: 2.59s	remaining: 1.16s
691:	learn: 0.4373954	total: 2.6s	remaining: 1.16s
692:	learn: 0.4373845	total: 2.6s	remaining: 1.15s
693:	learn: 0.4373712	total: 2.6s	remaining: 1.15s
694:	learn: 0.4373634	total: 2.61s	remaining: 1.14s
695:	learn: 0.4373393	total: 2.61s	remaining: 1.14s
696:	learn: 0.4373283	total: 2.61s	remaining: 1.14s
697:	learn: 0.4373178	total: 2.62s	remaining: 1.13s
698:	learn: 0.4373102	total: 2.62s	remaining: 1.13s
699:	learn: 0.4372976	total: 2.62s	remaining: 1.12s
700:	learn: 0.4372775	total: 2.63s	remaining: 1.12s
701:	learn: 0.4372604	total: 2.63s	remaining: 1.12s
702:	learn: 0.4372524	total: 2.63s	remaining: 1.11s
703:	learn: 0.4372297	total: 2.64s	remaining: 1.11s
704:	learn: 0.4372196	total: 2.64s	remaining: 1.1s
705:	learn: 0.4372083	total: 2.65s	remaining: 1.1s
706:	learn: 0.4371921	total: 2.65s	remaining: 1.1s
707:	learn: 0.4371818	total: 2.65s	remaining: 1.09s
708:	learn: 0.4371745	total: 2.66s	remaining: 1.09s
709:	learn: 0.4371

...

174:	learn: 0.4499164	total: 996ms	remaining: 4.7s
175:	learn: 0.4497603	total: 1s	remaining: 4.7s
176:	learn: 0.4497235	total: 1.01s	remaining: 4.7s
177:	learn: 0.4495872	total: 1.02s	remaining: 4.7s
178:	learn: 0.4494994	total: 1.02s	remaining: 4.7s
179:	learn: 0.4494529	total: 1.03s	remaining: 4.69s
180:	learn: 0.4494220	total: 1.04s	remaining: 4.69s
181:	learn: 0.4493376	total: 1.04s	remaining: 4.68s
182:	learn: 0.4492635	total: 1.05s	remaining: 4.67s
183:	learn: 0.4491923	total: 1.05s	remaining: 4.67s
184:	learn: 0.4491131	total: 1.06s	remaining: 4.66s
185:	learn: 0.4490113	total: 1.06s	remaining: 4.65s
186:	learn: 0.4488909	total: 1.07s	remaining: 4.64s
187:	learn: 0.4488612	total: 1.07s	remaining: 4.64s
188:	learn: 0.4487946	total: 1.08s	remaining: 4.63s
189:	learn: 0.4487037	total: 1.08s	remaining: 4.63s
190:	learn: 0.4486377	total: 1.09s	remaining: 4.63s
191:	learn: 0.4485874	total: 1.1s	remaining: 4.63s
192:	learn: 0.4484967	total: 1.1s	remaining: 4.62s
193:	learn: 0.4484603	

350:	learn: 0.4381368	total: 2.19s	remaining: 4.05s
351:	learn: 0.4381080	total: 2.2s	remaining: 4.04s
352:	learn: 0.4380646	total: 2.2s	remaining: 4.04s
353:	learn: 0.4380012	total: 2.21s	remaining: 4.03s
354:	learn: 0.4379391	total: 2.21s	remaining: 4.02s
355:	learn: 0.4378005	total: 2.22s	remaining: 4.01s
356:	learn: 0.4377077	total: 2.22s	remaining: 4.01s
357:	learn: 0.4376031	total: 2.23s	remaining: 4s
358:	learn: 0.4375287	total: 2.23s	remaining: 3.99s
359:	learn: 0.4373999	total: 2.24s	remaining: 3.98s
360:	learn: 0.4373782	total: 2.25s	remaining: 3.98s
361:	learn: 0.4373262	total: 2.25s	remaining: 3.97s
362:	learn: 0.4371994	total: 2.26s	remaining: 3.96s
363:	learn: 0.4371173	total: 2.26s	remaining: 3.95s
364:	learn: 0.4369789	total: 2.27s	remaining: 3.94s
365:	learn: 0.4368629	total: 2.27s	remaining: 3.94s
366:	learn: 0.4368370	total: 2.28s	remaining: 3.93s
367:	learn: 0.4367349	total: 2.28s	remaining: 3.92s
368:	learn: 0.4366449	total: 2.29s	remaining: 3.91s
369:	learn: 0.436

511:	learn: 0.4271420	total: 3.17s	remaining: 3.02s
512:	learn: 0.4270900	total: 3.17s	remaining: 3.01s
513:	learn: 0.4269680	total: 3.18s	remaining: 3.01s
514:	learn: 0.4268954	total: 3.19s	remaining: 3s
515:	learn: 0.4268284	total: 3.19s	remaining: 3s
516:	learn: 0.4268226	total: 3.2s	remaining: 2.99s
517:	learn: 0.4268132	total: 3.21s	remaining: 2.98s
518:	learn: 0.4267317	total: 3.21s	remaining: 2.98s
519:	learn: 0.4266596	total: 3.22s	remaining: 2.97s
520:	learn: 0.4266340	total: 3.23s	remaining: 2.96s
521:	learn: 0.4265379	total: 3.23s	remaining: 2.96s
522:	learn: 0.4265077	total: 3.24s	remaining: 2.95s
523:	learn: 0.4265032	total: 3.25s	remaining: 2.95s
524:	learn: 0.4264568	total: 3.26s	remaining: 2.95s
525:	learn: 0.4263587	total: 3.26s	remaining: 2.94s
526:	learn: 0.4262697	total: 3.27s	remaining: 2.94s
527:	learn: 0.4262515	total: 3.28s	remaining: 2.93s
528:	learn: 0.4261880	total: 3.28s	remaining: 2.92s
529:	learn: 0.4261633	total: 3.29s	remaining: 2.92s
530:	learn: 0.42611

675:	learn: 0.4199277	total: 4.14s	remaining: 1.99s
676:	learn: 0.4198546	total: 4.15s	remaining: 1.98s
677:	learn: 0.4198283	total: 4.15s	remaining: 1.97s
678:	learn: 0.4198274	total: 4.16s	remaining: 1.97s
679:	learn: 0.4197309	total: 4.17s	remaining: 1.96s
680:	learn: 0.4196416	total: 4.17s	remaining: 1.95s
681:	learn: 0.4195187	total: 4.18s	remaining: 1.95s
682:	learn: 0.4194325	total: 4.18s	remaining: 1.94s
683:	learn: 0.4193954	total: 4.19s	remaining: 1.93s
684:	learn: 0.4193685	total: 4.19s	remaining: 1.93s
685:	learn: 0.4192847	total: 4.2s	remaining: 1.92s
686:	learn: 0.4191771	total: 4.2s	remaining: 1.91s
687:	learn: 0.4191746	total: 4.21s	remaining: 1.91s
688:	learn: 0.4191285	total: 4.21s	remaining: 1.9s
689:	learn: 0.4190763	total: 4.22s	remaining: 1.89s
690:	learn: 0.4189549	total: 4.22s	remaining: 1.89s
691:	learn: 0.4189380	total: 4.23s	remaining: 1.88s
692:	learn: 0.4188006	total: 4.23s	remaining: 1.87s
693:	learn: 0.4187614	total: 4.24s	remaining: 1.87s
694:	learn: 0.4

864:	learn: 0.4117962	total: 5.14s	remaining: 802ms
865:	learn: 0.4117555	total: 5.15s	remaining: 796ms
866:	learn: 0.4117244	total: 5.15s	remaining: 790ms
867:	learn: 0.4117227	total: 5.16s	remaining: 785ms
868:	learn: 0.4116290	total: 5.18s	remaining: 780ms
869:	learn: 0.4115644	total: 5.19s	remaining: 775ms
870:	learn: 0.4115551	total: 5.19s	remaining: 769ms
871:	learn: 0.4115212	total: 5.2s	remaining: 763ms
872:	learn: 0.4115120	total: 5.21s	remaining: 757ms
873:	learn: 0.4114728	total: 5.21s	remaining: 752ms
874:	learn: 0.4114658	total: 5.22s	remaining: 746ms
875:	learn: 0.4114109	total: 5.22s	remaining: 739ms
876:	learn: 0.4113462	total: 5.23s	remaining: 733ms
877:	learn: 0.4113021	total: 5.23s	remaining: 727ms
878:	learn: 0.4112981	total: 5.24s	remaining: 721ms
879:	learn: 0.4112569	total: 5.24s	remaining: 715ms
880:	learn: 0.4112125	total: 5.25s	remaining: 709ms
881:	learn: 0.4112079	total: 5.25s	remaining: 703ms
882:	learn: 0.4111729	total: 5.26s	remaining: 697ms
883:	learn: 0

In [1031]:
scores

[0.5583966621129123,
 0.5567059511640222,
 0.5650920858442448,
 0.5635651373145647,
 0.570265765614514,
 0.5670644172981126]

In [1032]:
depth = depthes[np.argmax(scores)]
depth

6

In [1033]:
np.random.seed(0)
l_rates = (0.001, 0.0025, 0.005, 0.01, 0.05, 0.1)
scores = []
for rate in l_rates:
    model = catboost.CatBoostClassifier(depth=depth, learning_rate=rate)
    scores.append(cross_val_score(model, X_train, y_train, cv=5, scoring='f1').mean())

0:	learn: 0.6926001	total: 6.6ms	remaining: 6.6s
1:	learn: 0.6920551	total: 11.9ms	remaining: 5.96s
2:	learn: 0.6915227	total: 17ms	remaining: 5.64s
3:	learn: 0.6910049	total: 21.3ms	remaining: 5.3s
4:	learn: 0.6904774	total: 25.6ms	remaining: 5.1s
5:	learn: 0.6899383	total: 29.9ms	remaining: 4.96s
6:	learn: 0.6894190	total: 34.4ms	remaining: 4.88s
7:	learn: 0.6888968	total: 39.7ms	remaining: 4.92s
8:	learn: 0.6883705	total: 44.5ms	remaining: 4.9s
9:	learn: 0.6878307	total: 48.9ms	remaining: 4.84s
10:	learn: 0.6873023	total: 53ms	remaining: 4.77s
11:	learn: 0.6867881	total: 58.5ms	remaining: 4.82s
12:	learn: 0.6863035	total: 62.9ms	remaining: 4.78s
13:	learn: 0.6857872	total: 67.2ms	remaining: 4.73s
14:	learn: 0.6852732	total: 71.5ms	remaining: 4.69s
15:	learn: 0.6847573	total: 76.8ms	remaining: 4.73s
16:	learn: 0.6842248	total: 81.3ms	remaining: 4.7s
17:	learn: 0.6837223	total: 85.7ms	remaining: 4.68s
18:	learn: 0.6832108	total: 90ms	remaining: 4.64s
19:	learn: 0.6826869	total: 94.8ms

162:	learn: 0.6203138	total: 982ms	remaining: 5.04s
163:	learn: 0.6199381	total: 992ms	remaining: 5.06s
164:	learn: 0.6195582	total: 1.01s	remaining: 5.13s
165:	learn: 0.6191794	total: 1.02s	remaining: 5.13s
166:	learn: 0.6188027	total: 1.03s	remaining: 5.13s
167:	learn: 0.6184292	total: 1.04s	remaining: 5.14s
168:	learn: 0.6180643	total: 1.04s	remaining: 5.13s
169:	learn: 0.6177137	total: 1.05s	remaining: 5.13s
170:	learn: 0.6173628	total: 1.06s	remaining: 5.13s
171:	learn: 0.6169772	total: 1.06s	remaining: 5.11s
172:	learn: 0.6166239	total: 1.07s	remaining: 5.11s
173:	learn: 0.6162590	total: 1.07s	remaining: 5.09s
174:	learn: 0.6159168	total: 1.08s	remaining: 5.08s
175:	learn: 0.6155438	total: 1.09s	remaining: 5.1s
176:	learn: 0.6151773	total: 1.1s	remaining: 5.11s
177:	learn: 0.6148007	total: 1.1s	remaining: 5.09s
178:	learn: 0.6144230	total: 1.11s	remaining: 5.08s
179:	learn: 0.6140700	total: 1.12s	remaining: 5.1s
180:	learn: 0.6137339	total: 1.12s	remaining: 5.09s
181:	learn: 0.61

322:	learn: 0.5709640	total: 2s	remaining: 4.2s
323:	learn: 0.5707169	total: 2.01s	remaining: 4.2s
324:	learn: 0.5704473	total: 2.02s	remaining: 4.19s
325:	learn: 0.5701680	total: 2.02s	remaining: 4.18s
326:	learn: 0.5699173	total: 2.03s	remaining: 4.18s
327:	learn: 0.5696656	total: 2.04s	remaining: 4.18s
328:	learn: 0.5694005	total: 2.04s	remaining: 4.17s
329:	learn: 0.5691599	total: 2.05s	remaining: 4.17s
330:	learn: 0.5688994	total: 2.06s	remaining: 4.17s
331:	learn: 0.5686483	total: 2.07s	remaining: 4.17s
332:	learn: 0.5683957	total: 2.08s	remaining: 4.18s
333:	learn: 0.5681269	total: 2.1s	remaining: 4.18s
334:	learn: 0.5678739	total: 2.1s	remaining: 4.18s
335:	learn: 0.5676451	total: 2.12s	remaining: 4.19s
336:	learn: 0.5673941	total: 2.14s	remaining: 4.21s
337:	learn: 0.5671444	total: 2.15s	remaining: 4.21s
338:	learn: 0.5668902	total: 2.16s	remaining: 4.21s
339:	learn: 0.5666193	total: 2.17s	remaining: 4.21s
340:	learn: 0.5663698	total: 2.17s	remaining: 4.2s
341:	learn: 0.566130

511:	learn: 0.5314568	total: 3.2s	remaining: 3.05s
512:	learn: 0.5312734	total: 3.21s	remaining: 3.04s
513:	learn: 0.5311087	total: 3.21s	remaining: 3.04s
514:	learn: 0.5309400	total: 3.21s	remaining: 3.03s
515:	learn: 0.5307805	total: 3.22s	remaining: 3.02s
516:	learn: 0.5306339	total: 3.22s	remaining: 3.01s
517:	learn: 0.5304556	total: 3.23s	remaining: 3s
518:	learn: 0.5302712	total: 3.23s	remaining: 3s
519:	learn: 0.5300931	total: 3.24s	remaining: 2.99s
520:	learn: 0.5299306	total: 3.24s	remaining: 2.98s
521:	learn: 0.5297749	total: 3.25s	remaining: 2.98s
522:	learn: 0.5295962	total: 3.25s	remaining: 2.97s
523:	learn: 0.5294397	total: 3.26s	remaining: 2.96s
524:	learn: 0.5292810	total: 3.26s	remaining: 2.95s
525:	learn: 0.5291067	total: 3.27s	remaining: 2.95s
526:	learn: 0.5289426	total: 3.27s	remaining: 2.94s
527:	learn: 0.5287729	total: 3.28s	remaining: 2.93s
528:	learn: 0.5286057	total: 3.28s	remaining: 2.92s
529:	learn: 0.5284491	total: 3.29s	remaining: 2.92s
530:	learn: 0.52829

700:	learn: 0.5055078	total: 4.18s	remaining: 1.78s
701:	learn: 0.5053909	total: 4.19s	remaining: 1.78s
702:	learn: 0.5052834	total: 4.19s	remaining: 1.77s
703:	learn: 0.5051756	total: 4.2s	remaining: 1.76s
704:	learn: 0.5050663	total: 4.2s	remaining: 1.76s
705:	learn: 0.5049424	total: 4.21s	remaining: 1.75s
706:	learn: 0.5048342	total: 4.21s	remaining: 1.75s
707:	learn: 0.5047242	total: 4.22s	remaining: 1.74s
708:	learn: 0.5046194	total: 4.22s	remaining: 1.73s
709:	learn: 0.5045060	total: 4.23s	remaining: 1.73s
710:	learn: 0.5044005	total: 4.23s	remaining: 1.72s
711:	learn: 0.5042883	total: 4.24s	remaining: 1.71s
712:	learn: 0.5041933	total: 4.24s	remaining: 1.71s
713:	learn: 0.5040740	total: 4.24s	remaining: 1.7s
714:	learn: 0.5039578	total: 4.25s	remaining: 1.69s
715:	learn: 0.5038404	total: 4.25s	remaining: 1.69s
716:	learn: 0.5037282	total: 4.26s	remaining: 1.68s
717:	learn: 0.5036142	total: 4.26s	remaining: 1.67s
718:	learn: 0.5035029	total: 4.27s	remaining: 1.67s
719:	learn: 0.5

...

199:	learn: 0.4233575	total: 1.07s	remaining: 4.28s
200:	learn: 0.4229722	total: 1.08s	remaining: 4.28s
201:	learn: 0.4226040	total: 1.08s	remaining: 4.29s
202:	learn: 0.4223994	total: 1.09s	remaining: 4.28s
203:	learn: 0.4221636	total: 1.09s	remaining: 4.28s
204:	learn: 0.4221492	total: 1.1s	remaining: 4.26s
205:	learn: 0.4221337	total: 1.1s	remaining: 4.26s
206:	learn: 0.4220301	total: 1.11s	remaining: 4.25s
207:	learn: 0.4220107	total: 1.11s	remaining: 4.24s
208:	learn: 0.4218624	total: 1.12s	remaining: 4.23s
209:	learn: 0.4217210	total: 1.12s	remaining: 4.22s
210:	learn: 0.4216246	total: 1.13s	remaining: 4.22s
211:	learn: 0.4214397	total: 1.14s	remaining: 4.22s
212:	learn: 0.4214327	total: 1.14s	remaining: 4.22s
213:	learn: 0.4214265	total: 1.15s	remaining: 4.21s
214:	learn: 0.4212944	total: 1.15s	remaining: 4.2s
215:	learn: 0.4212202	total: 1.15s	remaining: 4.19s
216:	learn: 0.4210557	total: 1.16s	remaining: 4.18s
217:	learn: 0.4210491	total: 1.16s	remaining: 4.18s
218:	learn: 0.4

373:	learn: 0.4049181	total: 2.06s	remaining: 3.44s
374:	learn: 0.4047804	total: 2.06s	remaining: 3.44s
375:	learn: 0.4045904	total: 2.07s	remaining: 3.43s
376:	learn: 0.4045378	total: 2.07s	remaining: 3.42s
377:	learn: 0.4043541	total: 2.08s	remaining: 3.42s
378:	learn: 0.4042493	total: 2.08s	remaining: 3.41s
379:	learn: 0.4040270	total: 2.09s	remaining: 3.4s
380:	learn: 0.4038656	total: 2.09s	remaining: 3.4s
381:	learn: 0.4038100	total: 2.1s	remaining: 3.4s
382:	learn: 0.4037024	total: 2.1s	remaining: 3.39s
383:	learn: 0.4034907	total: 2.11s	remaining: 3.38s
384:	learn: 0.4034685	total: 2.11s	remaining: 3.38s
385:	learn: 0.4034579	total: 2.12s	remaining: 3.37s
386:	learn: 0.4034490	total: 2.12s	remaining: 3.36s
387:	learn: 0.4033910	total: 2.13s	remaining: 3.36s
388:	learn: 0.4033910	total: 2.13s	remaining: 3.35s
389:	learn: 0.4033802	total: 2.14s	remaining: 3.34s
390:	learn: 0.4032499	total: 2.14s	remaining: 3.34s
391:	learn: 0.4032492	total: 2.15s	remaining: 3.33s
392:	learn: 0.403

552:	learn: 0.3913312	total: 3.05s	remaining: 2.46s
553:	learn: 0.3912984	total: 3.06s	remaining: 2.46s
554:	learn: 0.3912742	total: 3.06s	remaining: 2.46s
555:	learn: 0.3912723	total: 3.07s	remaining: 2.45s
556:	learn: 0.3912012	total: 3.07s	remaining: 2.44s
557:	learn: 0.3910552	total: 3.08s	remaining: 2.44s
558:	learn: 0.3910450	total: 3.08s	remaining: 2.43s
559:	learn: 0.3908746	total: 3.09s	remaining: 2.43s
560:	learn: 0.3907647	total: 3.1s	remaining: 2.42s
561:	learn: 0.3906756	total: 3.1s	remaining: 2.42s
562:	learn: 0.3904681	total: 3.11s	remaining: 2.41s
563:	learn: 0.3904481	total: 3.12s	remaining: 2.41s
564:	learn: 0.3904365	total: 3.12s	remaining: 2.4s
565:	learn: 0.3902964	total: 3.12s	remaining: 2.4s
566:	learn: 0.3902056	total: 3.13s	remaining: 2.39s
567:	learn: 0.3900891	total: 3.13s	remaining: 2.38s
568:	learn: 0.3900879	total: 3.14s	remaining: 2.38s
569:	learn: 0.3899302	total: 3.14s	remaining: 2.37s
570:	learn: 0.3898905	total: 3.15s	remaining: 2.36s
571:	learn: 0.38

729:	learn: 0.3805140	total: 4.03s	remaining: 1.49s
730:	learn: 0.3804071	total: 4.04s	remaining: 1.49s
731:	learn: 0.3803206	total: 4.04s	remaining: 1.48s
732:	learn: 0.3802787	total: 4.05s	remaining: 1.48s
733:	learn: 0.3802747	total: 4.05s	remaining: 1.47s
734:	learn: 0.3801431	total: 4.06s	remaining: 1.46s
735:	learn: 0.3800707	total: 4.07s	remaining: 1.46s
736:	learn: 0.3800561	total: 4.07s	remaining: 1.45s
737:	learn: 0.3799518	total: 4.08s	remaining: 1.45s
738:	learn: 0.3799155	total: 4.08s	remaining: 1.44s
739:	learn: 0.3797940	total: 4.09s	remaining: 1.44s
740:	learn: 0.3797560	total: 4.09s	remaining: 1.43s
741:	learn: 0.3797429	total: 4.1s	remaining: 1.43s
742:	learn: 0.3795915	total: 4.1s	remaining: 1.42s
743:	learn: 0.3793450	total: 4.11s	remaining: 1.41s
744:	learn: 0.3791990	total: 4.11s	remaining: 1.41s
745:	learn: 0.3790815	total: 4.12s	remaining: 1.4s
746:	learn: 0.3789712	total: 4.13s	remaining: 1.4s
747:	learn: 0.3789058	total: 4.13s	remaining: 1.39s
748:	learn: 0.37

912:	learn: 0.3706988	total: 5.02s	remaining: 478ms
913:	learn: 0.3706981	total: 5.03s	remaining: 473ms
914:	learn: 0.3706169	total: 5.04s	remaining: 468ms
915:	learn: 0.3705789	total: 5.05s	remaining: 463ms
916:	learn: 0.3705561	total: 5.05s	remaining: 458ms
917:	learn: 0.3704814	total: 5.06s	remaining: 452ms
918:	learn: 0.3704569	total: 5.07s	remaining: 447ms
919:	learn: 0.3703944	total: 5.08s	remaining: 442ms
920:	learn: 0.3703850	total: 5.08s	remaining: 436ms
921:	learn: 0.3703823	total: 5.09s	remaining: 431ms
922:	learn: 0.3703763	total: 5.1s	remaining: 425ms
923:	learn: 0.3703628	total: 5.1s	remaining: 420ms
924:	learn: 0.3703606	total: 5.11s	remaining: 414ms
925:	learn: 0.3702901	total: 5.11s	remaining: 408ms
926:	learn: 0.3702598	total: 5.11s	remaining: 403ms
927:	learn: 0.3702578	total: 5.12s	remaining: 397ms
928:	learn: 0.3702530	total: 5.12s	remaining: 392ms
929:	learn: 0.3702485	total: 5.13s	remaining: 386ms
930:	learn: 0.3702297	total: 5.13s	remaining: 381ms
931:	learn: 0.

In [1034]:
scores

[0.5432932582554286,
 0.5473742777420745,
 0.5487689569737599,
 0.5539863166639586,
 0.566179696922482,
 0.5606494007233674]

In [1035]:
l_rate = l_rates[np.argmax(scores)]
l_rate

0.05

In [1036]:
np.random.seed(0)
Сoefficients = (21500, 22000, 25000, 28000, 28500)
scores = []
for C in Сoefficients:
    model = catboost.CatBoostClassifier(depth=depth, learning_rate=l_rate, l2_leaf_reg=C)
    scores.append(cross_val_score(model, X_train, y_train, cv=5, scoring='f1').mean())

0:	learn: 0.6879196	total: 4.5ms	remaining: 4.5s
1:	learn: 0.6826232	total: 10.2ms	remaining: 5.09s
2:	learn: 0.6769919	total: 14.6ms	remaining: 4.85s
3:	learn: 0.6718174	total: 18.8ms	remaining: 4.67s
4:	learn: 0.6668668	total: 22.8ms	remaining: 4.55s
5:	learn: 0.6631021	total: 27.1ms	remaining: 4.48s
6:	learn: 0.6593721	total: 32.5ms	remaining: 4.62s
7:	learn: 0.6551351	total: 38.4ms	remaining: 4.76s
8:	learn: 0.6505118	total: 44.2ms	remaining: 4.87s
9:	learn: 0.6464687	total: 49.9ms	remaining: 4.94s
10:	learn: 0.6420266	total: 54.1ms	remaining: 4.87s
11:	learn: 0.6379155	total: 58.2ms	remaining: 4.79s
12:	learn: 0.6329241	total: 62.8ms	remaining: 4.77s
13:	learn: 0.6290058	total: 67.2ms	remaining: 4.73s
14:	learn: 0.6252117	total: 72.2ms	remaining: 4.74s
15:	learn: 0.6211115	total: 77.1ms	remaining: 4.74s
16:	learn: 0.6170078	total: 82.2ms	remaining: 4.75s
17:	learn: 0.6139706	total: 88ms	remaining: 4.8s
18:	learn: 0.6099090	total: 92.3ms	remaining: 4.77s
19:	learn: 0.6067360	total:

192:	learn: 0.4662294	total: 991ms	remaining: 4.14s
193:	learn: 0.4661036	total: 997ms	remaining: 4.14s
194:	learn: 0.4659518	total: 1s	remaining: 4.14s
195:	learn: 0.4658216	total: 1.01s	remaining: 4.13s
196:	learn: 0.4657058	total: 1.01s	remaining: 4.12s
197:	learn: 0.4655655	total: 1.02s	remaining: 4.12s
198:	learn: 0.4654438	total: 1.02s	remaining: 4.11s
199:	learn: 0.4653063	total: 1.02s	remaining: 4.1s
200:	learn: 0.4651730	total: 1.03s	remaining: 4.09s
201:	learn: 0.4650698	total: 1.03s	remaining: 4.09s
202:	learn: 0.4649385	total: 1.04s	remaining: 4.08s
203:	learn: 0.4648105	total: 1.04s	remaining: 4.08s
204:	learn: 0.4646728	total: 1.05s	remaining: 4.07s
205:	learn: 0.4645422	total: 1.05s	remaining: 4.06s
206:	learn: 0.4644325	total: 1.06s	remaining: 4.05s
207:	learn: 0.4643027	total: 1.06s	remaining: 4.04s
208:	learn: 0.4641705	total: 1.07s	remaining: 4.04s
209:	learn: 0.4640421	total: 1.07s	remaining: 4.03s
210:	learn: 0.4639153	total: 1.07s	remaining: 4.02s
211:	learn: 0.46

377:	learn: 0.4542161	total: 1.97s	remaining: 3.25s
378:	learn: 0.4541798	total: 1.98s	remaining: 3.25s
379:	learn: 0.4541460	total: 1.99s	remaining: 3.24s
380:	learn: 0.4541173	total: 1.99s	remaining: 3.24s
381:	learn: 0.4540898	total: 2s	remaining: 3.23s
382:	learn: 0.4540531	total: 2s	remaining: 3.23s
383:	learn: 0.4540248	total: 2.01s	remaining: 3.22s
384:	learn: 0.4539910	total: 2.01s	remaining: 3.21s
385:	learn: 0.4539582	total: 2.02s	remaining: 3.21s
386:	learn: 0.4539244	total: 2.02s	remaining: 3.2s
387:	learn: 0.4538919	total: 2.02s	remaining: 3.19s
388:	learn: 0.4538518	total: 2.03s	remaining: 3.19s
389:	learn: 0.4538124	total: 2.03s	remaining: 3.18s
390:	learn: 0.4537850	total: 2.04s	remaining: 3.17s
391:	learn: 0.4537614	total: 2.04s	remaining: 3.17s
392:	learn: 0.4537297	total: 2.05s	remaining: 3.16s
393:	learn: 0.4537063	total: 2.05s	remaining: 3.16s
394:	learn: 0.4536784	total: 2.06s	remaining: 3.15s
395:	learn: 0.4536460	total: 2.06s	remaining: 3.15s
396:	learn: 0.45361

557:	learn: 0.4497448	total: 3.15s	remaining: 2.5s
558:	learn: 0.4497282	total: 3.16s	remaining: 2.5s
559:	learn: 0.4497108	total: 3.17s	remaining: 2.49s
560:	learn: 0.4496941	total: 3.18s	remaining: 2.49s
561:	learn: 0.4496790	total: 3.19s	remaining: 2.48s
562:	learn: 0.4496640	total: 3.2s	remaining: 2.48s
563:	learn: 0.4496429	total: 3.21s	remaining: 2.48s
564:	learn: 0.4496297	total: 3.21s	remaining: 2.47s
565:	learn: 0.4496148	total: 3.22s	remaining: 2.47s
566:	learn: 0.4496004	total: 3.23s	remaining: 2.47s
567:	learn: 0.4495842	total: 3.24s	remaining: 2.46s
568:	learn: 0.4495692	total: 3.25s	remaining: 2.46s
569:	learn: 0.4495525	total: 3.25s	remaining: 2.45s
570:	learn: 0.4495368	total: 3.25s	remaining: 2.45s
571:	learn: 0.4495222	total: 3.26s	remaining: 2.44s
572:	learn: 0.4494973	total: 3.26s	remaining: 2.43s
573:	learn: 0.4494839	total: 3.27s	remaining: 2.42s
574:	learn: 0.4494686	total: 3.27s	remaining: 2.42s
575:	learn: 0.4494543	total: 3.28s	remaining: 2.41s
576:	learn: 0.4

726:	learn: 0.4474860	total: 4.14s	remaining: 1.55s
727:	learn: 0.4474736	total: 4.15s	remaining: 1.55s
728:	learn: 0.4474641	total: 4.15s	remaining: 1.54s
729:	learn: 0.4474522	total: 4.16s	remaining: 1.54s
730:	learn: 0.4474390	total: 4.16s	remaining: 1.53s
731:	learn: 0.4474299	total: 4.17s	remaining: 1.53s
732:	learn: 0.4474190	total: 4.17s	remaining: 1.52s
733:	learn: 0.4474101	total: 4.18s	remaining: 1.51s
734:	learn: 0.4473990	total: 4.18s	remaining: 1.51s
735:	learn: 0.4473904	total: 4.19s	remaining: 1.5s
736:	learn: 0.4473788	total: 4.19s	remaining: 1.5s
737:	learn: 0.4473686	total: 4.2s	remaining: 1.49s
738:	learn: 0.4473596	total: 4.2s	remaining: 1.48s
739:	learn: 0.4473493	total: 4.22s	remaining: 1.48s
740:	learn: 0.4473403	total: 4.24s	remaining: 1.48s
741:	learn: 0.4473315	total: 4.25s	remaining: 1.48s
742:	learn: 0.4473214	total: 4.26s	remaining: 1.47s
743:	learn: 0.4473078	total: 4.28s	remaining: 1.47s
744:	learn: 0.4472988	total: 4.29s	remaining: 1.47s
745:	learn: 0.44

...

251:	learn: 0.4829846	total: 1.28s	remaining: 3.79s
252:	learn: 0.4828749	total: 1.28s	remaining: 3.79s
253:	learn: 0.4827662	total: 1.29s	remaining: 3.79s
254:	learn: 0.4826733	total: 1.29s	remaining: 3.79s
255:	learn: 0.4825940	total: 1.3s	remaining: 3.78s
256:	learn: 0.4824881	total: 1.3s	remaining: 3.77s
257:	learn: 0.4823755	total: 1.31s	remaining: 3.76s
258:	learn: 0.4822699	total: 1.31s	remaining: 3.76s
259:	learn: 0.4821658	total: 1.32s	remaining: 3.75s
260:	learn: 0.4820619	total: 1.32s	remaining: 3.75s
261:	learn: 0.4819770	total: 1.33s	remaining: 3.74s
262:	learn: 0.4818758	total: 1.33s	remaining: 3.73s
263:	learn: 0.4818014	total: 1.34s	remaining: 3.73s
264:	learn: 0.4817003	total: 1.34s	remaining: 3.72s
265:	learn: 0.4816199	total: 1.34s	remaining: 3.71s
266:	learn: 0.4815340	total: 1.35s	remaining: 3.71s
267:	learn: 0.4814289	total: 1.35s	remaining: 3.7s
268:	learn: 0.4813503	total: 1.36s	remaining: 3.7s
269:	learn: 0.4812525	total: 1.36s	remaining: 3.69s
270:	learn: 0.48

437:	learn: 0.4715172	total: 2.27s	remaining: 2.91s
438:	learn: 0.4714928	total: 2.27s	remaining: 2.9s
439:	learn: 0.4714695	total: 2.28s	remaining: 2.9s
440:	learn: 0.4714304	total: 2.28s	remaining: 2.9s
441:	learn: 0.4713946	total: 2.29s	remaining: 2.89s
442:	learn: 0.4713587	total: 2.29s	remaining: 2.88s
443:	learn: 0.4713179	total: 2.3s	remaining: 2.88s
444:	learn: 0.4712800	total: 2.3s	remaining: 2.87s
445:	learn: 0.4712449	total: 2.31s	remaining: 2.87s
446:	learn: 0.4712224	total: 2.31s	remaining: 2.86s
447:	learn: 0.4711874	total: 2.32s	remaining: 2.86s
448:	learn: 0.4711489	total: 2.32s	remaining: 2.85s
449:	learn: 0.4711118	total: 2.33s	remaining: 2.84s
450:	learn: 0.4710716	total: 2.33s	remaining: 2.84s
451:	learn: 0.4710496	total: 2.34s	remaining: 2.83s
452:	learn: 0.4710152	total: 2.34s	remaining: 2.83s
453:	learn: 0.4709934	total: 2.35s	remaining: 2.82s
454:	learn: 0.4709714	total: 2.35s	remaining: 2.81s
455:	learn: 0.4709190	total: 2.35s	remaining: 2.81s
456:	learn: 0.470

600:	learn: 0.4676446	total: 3.06s	remaining: 2.03s
601:	learn: 0.4676291	total: 3.07s	remaining: 2.03s
602:	learn: 0.4676136	total: 3.07s	remaining: 2.02s
603:	learn: 0.4675966	total: 3.08s	remaining: 2.02s
604:	learn: 0.4675809	total: 3.08s	remaining: 2.01s
605:	learn: 0.4675651	total: 3.09s	remaining: 2.01s
606:	learn: 0.4675495	total: 3.09s	remaining: 2s
607:	learn: 0.4675319	total: 3.1s	remaining: 2s
608:	learn: 0.4675153	total: 3.1s	remaining: 1.99s
609:	learn: 0.4674990	total: 3.1s	remaining: 1.99s
610:	learn: 0.4674858	total: 3.11s	remaining: 1.98s
611:	learn: 0.4674606	total: 3.12s	remaining: 1.98s
612:	learn: 0.4674353	total: 3.12s	remaining: 1.97s
613:	learn: 0.4674198	total: 3.12s	remaining: 1.96s
614:	learn: 0.4674045	total: 3.13s	remaining: 1.96s
615:	learn: 0.4673844	total: 3.13s	remaining: 1.95s
616:	learn: 0.4673678	total: 3.14s	remaining: 1.95s
617:	learn: 0.4673527	total: 3.14s	remaining: 1.94s
618:	learn: 0.4673357	total: 3.15s	remaining: 1.94s
619:	learn: 0.4673188

793:	learn: 0.4648230	total: 4.05s	remaining: 1.05s
794:	learn: 0.4648123	total: 4.05s	remaining: 1.04s
795:	learn: 0.4648020	total: 4.06s	remaining: 1.04s
796:	learn: 0.4647876	total: 4.06s	remaining: 1.03s
797:	learn: 0.4647763	total: 4.07s	remaining: 1.03s
798:	learn: 0.4647616	total: 4.08s	remaining: 1.02s
799:	learn: 0.4647439	total: 4.08s	remaining: 1.02s
800:	learn: 0.4647327	total: 4.08s	remaining: 1.01s
801:	learn: 0.4647227	total: 4.09s	remaining: 1.01s
802:	learn: 0.4647143	total: 4.09s	remaining: 1s
803:	learn: 0.4647044	total: 4.1s	remaining: 999ms
804:	learn: 0.4646943	total: 4.1s	remaining: 994ms
805:	learn: 0.4646814	total: 4.11s	remaining: 989ms
806:	learn: 0.4646721	total: 4.11s	remaining: 984ms
807:	learn: 0.4646541	total: 4.12s	remaining: 978ms
808:	learn: 0.4646443	total: 4.12s	remaining: 974ms
809:	learn: 0.4646344	total: 4.13s	remaining: 969ms
810:	learn: 0.4646233	total: 4.13s	remaining: 963ms
811:	learn: 0.4646130	total: 4.14s	remaining: 958ms
812:	learn: 0.464

980:	learn: 0.4629539	total: 5.04s	remaining: 97.6ms
981:	learn: 0.4629459	total: 5.04s	remaining: 92.5ms
982:	learn: 0.4629375	total: 5.05s	remaining: 87.3ms
983:	learn: 0.4629291	total: 5.05s	remaining: 82.2ms
984:	learn: 0.4629222	total: 5.06s	remaining: 77ms
985:	learn: 0.4629156	total: 5.06s	remaining: 71.9ms
986:	learn: 0.4629029	total: 5.07s	remaining: 66.8ms
987:	learn: 0.4628957	total: 5.07s	remaining: 61.6ms
988:	learn: 0.4628833	total: 5.08s	remaining: 56.5ms
989:	learn: 0.4628750	total: 5.08s	remaining: 51.4ms
990:	learn: 0.4628668	total: 5.09s	remaining: 46.2ms
991:	learn: 0.4628603	total: 5.09s	remaining: 41.1ms
992:	learn: 0.4628496	total: 5.1s	remaining: 35.9ms
993:	learn: 0.4628425	total: 5.1s	remaining: 30.8ms
994:	learn: 0.4628300	total: 5.11s	remaining: 25.7ms
995:	learn: 0.4628232	total: 5.11s	remaining: 20.5ms
996:	learn: 0.4628150	total: 5.12s	remaining: 15.4ms
997:	learn: 0.4628069	total: 5.12s	remaining: 10.3ms
998:	learn: 0.4628002	total: 5.13s	remaining: 5.13

In [1037]:
scores

[0.554362539072008,
 0.5544116118416309,
 0.5531953044560289,
 0.5519280951565276,
 0.5519977668464173]

In [1038]:
reg = Сoefficients[np.argmax(scores)]
reg

22000

In [1039]:
np.random.seed(0)
trees = (1, 2, 3, 5, 6, 7, 8, 9, 10)
scores = []
for tree in trees:
    model = catboost.CatBoostClassifier(depth=depth, learning_rate=l_rate, l2_leaf_reg=reg, num_trees=tree)
    scores.append(cross_val_score(model, X_train, y_train, cv=5, scoring='f1').mean())

0:	learn: 0.6880184	total: 5.05ms	remaining: 0us
0:	learn: 0.6883544	total: 4.63ms	remaining: 0us
0:	learn: 0.6883788	total: 4.12ms	remaining: 0us
0:	learn: 0.6887648	total: 6.46ms	remaining: 0us
0:	learn: 0.6892019	total: 4.72ms	remaining: 0us
0:	learn: 0.6880184	total: 6.04ms	remaining: 6.04ms
1:	learn: 0.6828196	total: 12ms	remaining: 0us
0:	learn: 0.6883544	total: 7.42ms	remaining: 7.42ms
1:	learn: 0.6846385	total: 14.5ms	remaining: 0us
0:	learn: 0.6883788	total: 4.55ms	remaining: 4.55ms
1:	learn: 0.6842273	total: 10.2ms	remaining: 0us
0:	learn: 0.6887648	total: 16.5ms	remaining: 16.5ms
1:	learn: 0.6848511	total: 21.2ms	remaining: 0us
0:	learn: 0.6892019	total: 4.09ms	remaining: 4.09ms
1:	learn: 0.6842910	total: 8.27ms	remaining: 0us
0:	learn: 0.6880184	total: 4.58ms	remaining: 9.16ms
1:	learn: 0.6828196	total: 8.88ms	remaining: 4.44ms
2:	learn: 0.6772867	total: 14.1ms	remaining: 0us
0:	learn: 0.6883544	total: 4.23ms	remaining: 8.45ms
1:	learn: 0.6846385	total: 9.74ms	remaining: 4.

0:	learn: 0.6883544	total: 6.61ms	remaining: 52.9ms
1:	learn: 0.6846385	total: 11.3ms	remaining: 39.4ms
2:	learn: 0.6795393	total: 16ms	remaining: 32ms
3:	learn: 0.6748384	total: 20.3ms	remaining: 25.3ms
4:	learn: 0.6701502	total: 24.5ms	remaining: 19.6ms
5:	learn: 0.6665353	total: 28.6ms	remaining: 14.3ms
6:	learn: 0.6630012	total: 32.8ms	remaining: 9.38ms
7:	learn: 0.6589711	total: 38.2ms	remaining: 4.77ms
8:	learn: 0.6546369	total: 42.8ms	remaining: 0us
0:	learn: 0.6883788	total: 4.53ms	remaining: 36.2ms
1:	learn: 0.6842273	total: 9.1ms	remaining: 31.9ms
2:	learn: 0.6806420	total: 13.4ms	remaining: 26.9ms
3:	learn: 0.6758598	total: 17.6ms	remaining: 22ms
4:	learn: 0.6712078	total: 22.9ms	remaining: 18.3ms
5:	learn: 0.6676596	total: 27.2ms	remaining: 13.6ms
6:	learn: 0.6641288	total: 31.5ms	remaining: 9ms
7:	learn: 0.6601114	total: 35.5ms	remaining: 4.44ms
8:	learn: 0.6558121	total: 40.2ms	remaining: 0us
0:	learn: 0.6887648	total: 4.28ms	remaining: 34.3ms
1:	learn: 0.6848511	total: 9

In [1040]:
scores

[0.5798606292623443,
 0.582437014594807,
 0.5822381200508318,
 0.5685818267490748,
 0.5722393106779549,
 0.5756156150590976,
 0.5654063695737738,
 0.5649800316418687,
 0.5533866521827526]

In [1041]:
tree = trees[np.argmax(scores)]
tree

2

In [1042]:
np.random.seed(0)
etas = (0.001, 0.0001, 0.005)
scores = []
for eta in etas:
    model = catboost.CatBoostClassifier(depth=depth, l2_leaf_reg=reg, num_trees=tree, eta=eta)
    scores.append(cross_val_score(model, X_train, y_train, cv=5, scoring='f1').mean())

0:	learn: 0.6930439	total: 4.55ms	remaining: 4.55ms
1:	learn: 0.6929366	total: 9.12ms	remaining: 0us
0:	learn: 0.6930507	total: 4.53ms	remaining: 4.53ms
1:	learn: 0.6929743	total: 8.84ms	remaining: 0us
0:	learn: 0.6930512	total: 5.1ms	remaining: 5.1ms
1:	learn: 0.6929482	total: 9.28ms	remaining: 0us
0:	learn: 0.6930591	total: 4.49ms	remaining: 4.49ms
1:	learn: 0.6929788	total: 9.27ms	remaining: 0us
0:	learn: 0.6930678	total: 6.02ms	remaining: 6.02ms
1:	learn: 0.6928997	total: 12.7ms	remaining: 0us
0:	learn: 0.6931369	total: 4.36ms	remaining: 4.36ms
1:	learn: 0.6931261	total: 9.48ms	remaining: 0us
0:	learn: 0.6931375	total: 6.36ms	remaining: 6.36ms
1:	learn: 0.6931299	total: 11.1ms	remaining: 0us
0:	learn: 0.6931376	total: 4.12ms	remaining: 4.12ms
1:	learn: 0.6931273	total: 8.38ms	remaining: 0us
0:	learn: 0.6931384	total: 4.7ms	remaining: 4.7ms
1:	learn: 0.6931303	total: 8.82ms	remaining: 0us
0:	learn: 0.6931392	total: 6.27ms	remaining: 6.27ms
1:	learn: 0.6931224	total: 13.8ms	remaining

In [1043]:
scores

[0.5856422758870213, 0.5856422758870213, 0.5856422758870213]

In [1044]:
eta = etas[np.argmax(scores)]
eta

0.001

In [1045]:
np.random.seed(0)
scales = (1.9, 2, 2.1, 2.2, 2.3, 2.4, 2.5, 2.45, 2.35, 2.55, 2.6, 2.7, 2.8, 2.9, 3)
scores = []
for scale in scales:
    model = catboost.CatBoostClassifier(depth=depth, l2_leaf_reg=reg, num_trees=tree, eta=eta, scale_pos_weight=scale,
                                       mvs_reg=mvs_reg)
    scores.append(cross_val_score(model, X_train, y_train, cv=5, scoring='f1').mean())

0:	learn: 0.6930802	total: 4.2ms	remaining: 4.2ms
1:	learn: 0.6930164	total: 8.56ms	remaining: 0us
0:	learn: 0.6930855	total: 4.24ms	remaining: 4.24ms
1:	learn: 0.6930316	total: 9.93ms	remaining: 0us
0:	learn: 0.6930843	total: 4.68ms	remaining: 4.68ms
1:	learn: 0.6930092	total: 10.3ms	remaining: 0us
0:	learn: 0.6930835	total: 6.68ms	remaining: 6.68ms
1:	learn: 0.6930172	total: 11.9ms	remaining: 0us
0:	learn: 0.6930885	total: 4.87ms	remaining: 4.87ms
1:	learn: 0.6930169	total: 11.9ms	remaining: 0us
0:	learn: 0.6930817	total: 4.21ms	remaining: 4.21ms
1:	learn: 0.6930102	total: 8.76ms	remaining: 0us
0:	learn: 0.6930869	total: 6.12ms	remaining: 6.12ms
1:	learn: 0.6930312	total: 15ms	remaining: 0us
0:	learn: 0.6930874	total: 4.72ms	remaining: 4.72ms
1:	learn: 0.6930137	total: 9.22ms	remaining: 0us
0:	learn: 0.6930847	total: 6.85ms	remaining: 6.85ms
1:	learn: 0.6930188	total: 14.1ms	remaining: 0us
0:	learn: 0.6930697	total: 14.8ms	remaining: 14.8ms
1:	learn: 0.6929997	total: 21.3ms	remaining

In [1046]:
scores

[0.6275282359325233,
 0.6236794135718683,
 0.627563633926677,
 0.6274393018920172,
 0.6292647794404803,
 0.6291869089193076,
 0.6294486731495793,
 0.6291869089193076,
 0.6292647794404803,
 0.6294618088777748,
 0.6292000446475031,
 0.6289038766769226,
 0.6300161190232234,
 0.6279663512844633,
 0.6239202225671387]

In [1047]:
scale = scales[np.argmax(scores)]
scale

2.8

Повторный прогон

In [1070]:
np.random.seed(0)
depthes = (2, 3, 4, 5, 6, 7)
scores = []
for depth in depthes:
    model = catboost.CatBoostClassifier(depth=depth, l2_leaf_reg=reg, num_trees=tree, eta=eta, scale_pos_weight=scale,
                                       mvs_reg=mvs_reg)
    scores.append(cross_val_score(model, X_train, y_train, cv=5, scoring='f1').mean())

0:	learn: 0.6930458	total: 3.55ms	remaining: 3.55ms
1:	learn: 0.6929477	total: 7.28ms	remaining: 0us
0:	learn: 0.6930544	total: 3.3ms	remaining: 3.3ms
1:	learn: 0.6929565	total: 6.97ms	remaining: 0us
0:	learn: 0.6930570	total: 4.07ms	remaining: 4.07ms
1:	learn: 0.6929634	total: 7.59ms	remaining: 0us
0:	learn: 0.6930488	total: 4.28ms	remaining: 4.28ms
1:	learn: 0.6929527	total: 12.4ms	remaining: 0us
0:	learn: 0.6930640	total: 4.28ms	remaining: 4.28ms
1:	learn: 0.6929758	total: 7.8ms	remaining: 0us
0:	learn: 0.6930480	total: 3.58ms	remaining: 3.58ms
1:	learn: 0.6929464	total: 8.02ms	remaining: 0us
0:	learn: 0.6930562	total: 7.22ms	remaining: 7.22ms
1:	learn: 0.6929620	total: 11.8ms	remaining: 0us
0:	learn: 0.6930589	total: 5.2ms	remaining: 5.2ms
1:	learn: 0.6929671	total: 9.07ms	remaining: 0us
0:	learn: 0.6930517	total: 4.07ms	remaining: 4.07ms
1:	learn: 0.6929683	total: 7.76ms	remaining: 0us
0:	learn: 0.6930661	total: 4.95ms	remaining: 4.95ms
1:	learn: 0.6929877	total: 9.8ms	remaining: 

In [1071]:
scores

[0.6259300011029041,
 0.6218678269161588,
 0.6240594510334818,
 0.625179452548155,
 0.6300161190232234,
 0.6270375685451268]

In [1072]:
depth = depthes[np.argmax(scores)]
depth

6

In [1073]:
np.random.seed(0)
trees = (1, 2, 3, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14)
scores = []
for tree in trees:
    model = catboost.CatBoostClassifier(depth=depth, l2_leaf_reg=reg, num_trees=tree, eta=eta, scale_pos_weight=scale,
                                       mvs_reg=mvs_reg)
    scores.append(cross_val_score(model, X_train, y_train, cv=5, scoring='f1').mean())

0:	learn: 0.6930842	total: 11ms	remaining: 0us
0:	learn: 0.6930606	total: 6.24ms	remaining: 0us
0:	learn: 0.6930890	total: 4.41ms	remaining: 0us
0:	learn: 0.6930644	total: 8.33ms	remaining: 0us
0:	learn: 0.6930684	total: 9.75ms	remaining: 0us
0:	learn: 0.6930842	total: 4.51ms	remaining: 4.51ms
1:	learn: 0.6930114	total: 8.97ms	remaining: 0us
0:	learn: 0.6930606	total: 6.94ms	remaining: 6.94ms
1:	learn: 0.6930017	total: 11.8ms	remaining: 0us
0:	learn: 0.6930890	total: 4.68ms	remaining: 4.68ms
1:	learn: 0.6930265	total: 9.31ms	remaining: 0us
0:	learn: 0.6930644	total: 4.31ms	remaining: 4.31ms
1:	learn: 0.6929942	total: 9.62ms	remaining: 0us
0:	learn: 0.6930684	total: 7.46ms	remaining: 7.46ms
1:	learn: 0.6930010	total: 13.5ms	remaining: 0us
0:	learn: 0.6930842	total: 4.62ms	remaining: 9.23ms
1:	learn: 0.6930114	total: 9.7ms	remaining: 4.85ms
2:	learn: 0.6929302	total: 14.3ms	remaining: 0us
0:	learn: 0.6930606	total: 4.86ms	remaining: 9.71ms
1:	learn: 0.6930017	total: 9.35ms	remaining: 4.6

0:	learn: 0.6930890	total: 8.91ms	remaining: 71.3ms
1:	learn: 0.6930265	total: 14.8ms	remaining: 52ms
2:	learn: 0.6929745	total: 20.4ms	remaining: 40.8ms
3:	learn: 0.6929001	total: 25.6ms	remaining: 32ms
4:	learn: 0.6928213	total: 30ms	remaining: 24ms
5:	learn: 0.6927779	total: 34.3ms	remaining: 17.2ms
6:	learn: 0.6927182	total: 38.5ms	remaining: 11ms
7:	learn: 0.6926490	total: 43.4ms	remaining: 5.43ms
8:	learn: 0.6925818	total: 47.7ms	remaining: 0us
0:	learn: 0.6930644	total: 4.45ms	remaining: 35.6ms
1:	learn: 0.6929942	total: 8.86ms	remaining: 31ms
2:	learn: 0.6929490	total: 13.3ms	remaining: 26.6ms
3:	learn: 0.6928649	total: 18.9ms	remaining: 23.6ms
4:	learn: 0.6927763	total: 23.7ms	remaining: 18.9ms
5:	learn: 0.6927117	total: 28.2ms	remaining: 14.1ms
6:	learn: 0.6926427	total: 34.2ms	remaining: 9.76ms
7:	learn: 0.6925572	total: 40.8ms	remaining: 5.11ms
8:	learn: 0.6924812	total: 47ms	remaining: 0us
0:	learn: 0.6930684	total: 4.5ms	remaining: 36ms
1:	learn: 0.6930010	total: 11.6ms	r

0:	learn: 0.6930644	total: 9.54ms	remaining: 105ms
1:	learn: 0.6929942	total: 23.5ms	remaining: 117ms
2:	learn: 0.6929490	total: 31.1ms	remaining: 93.2ms
3:	learn: 0.6928649	total: 40.3ms	remaining: 80.6ms
4:	learn: 0.6927763	total: 50.4ms	remaining: 70.6ms
5:	learn: 0.6927117	total: 57.6ms	remaining: 57.6ms
6:	learn: 0.6926427	total: 64.5ms	remaining: 46.1ms
7:	learn: 0.6925572	total: 69.4ms	remaining: 34.7ms
8:	learn: 0.6924812	total: 74.9ms	remaining: 25ms
9:	learn: 0.6924239	total: 81.4ms	remaining: 16.3ms
10:	learn: 0.6923398	total: 85.8ms	remaining: 7.8ms
11:	learn: 0.6922732	total: 90.4ms	remaining: 0us
0:	learn: 0.6930684	total: 7.11ms	remaining: 78.2ms
1:	learn: 0.6930010	total: 15.3ms	remaining: 76.6ms
2:	learn: 0.6929513	total: 20.3ms	remaining: 61ms
3:	learn: 0.6928770	total: 25.2ms	remaining: 50.4ms
4:	learn: 0.6928030	total: 29.4ms	remaining: 41.2ms
5:	learn: 0.6927610	total: 33.9ms	remaining: 33.9ms
6:	learn: 0.6927069	total: 41.4ms	remaining: 29.6ms
7:	learn: 0.6926306	

In [1074]:
scores

[0.6230163499637887,
 0.6300161190232234,
 0.6289038766769226,
 0.6266554507163644,
 0.6249594306329694,
 0.6250289596415328,
 0.6248312524333869,
 0.6241154298511965,
 0.6248232227659701,
 0.625408280855017,
 0.6248882611805987,
 0.6232189855837678,
 0.6234859503783012]

In [1075]:
tree = trees[np.argmax(scores)]
tree

2

In [1076]:
np.random.seed(0)
Сoefficients = (15000, 21500, 22000, 22500, 23000, 24000, 25000)
scores = []
for C in Сoefficients:
    model = catboost.CatBoostClassifier(depth=depth, num_trees=tree, eta=eta, scale_pos_weight=scale, l2_leaf_reg=C,
                                        mvs_reg=mvs_reg)
    scores.append(cross_val_score(model, X_train, y_train, cv=5, scoring='f1').mean())

0:	learn: 0.6930616	total: 5.58ms	remaining: 5.58ms
1:	learn: 0.6929637	total: 11.8ms	remaining: 0us
0:	learn: 0.6930334	total: 5.63ms	remaining: 5.63ms
1:	learn: 0.6929533	total: 10.5ms	remaining: 0us
0:	learn: 0.6930682	total: 4.33ms	remaining: 4.33ms
1:	learn: 0.6929837	total: 8.79ms	remaining: 0us
0:	learn: 0.6930581	total: 4.38ms	remaining: 4.38ms
1:	learn: 0.6929631	total: 9.46ms	remaining: 0us
0:	learn: 0.6930435	total: 4.35ms	remaining: 4.35ms
1:	learn: 0.6929635	total: 9.62ms	remaining: 0us
0:	learn: 0.6930842	total: 4.96ms	remaining: 4.96ms
1:	learn: 0.6930114	total: 10.1ms	remaining: 0us
0:	learn: 0.6930606	total: 10ms	remaining: 10ms
1:	learn: 0.6930017	total: 16.3ms	remaining: 0us
0:	learn: 0.6930890	total: 5.08ms	remaining: 5.08ms
1:	learn: 0.6930265	total: 10.8ms	remaining: 0us
0:	learn: 0.6930644	total: 5.82ms	remaining: 5.82ms
1:	learn: 0.6929942	total: 12.8ms	remaining: 0us
0:	learn: 0.6930684	total: 5.06ms	remaining: 5.06ms
1:	learn: 0.6930010	total: 9.6ms	remaining:

In [1077]:
scores

[0.6289038766769226,
 0.6300161190232234,
 0.6300161190232234,
 0.6300161190232234,
 0.6300161190232234,
 0.6300161190232234,
 0.6300161190232234]

In [1078]:
reg=Сoefficients[np.argmax(scores)]
reg

21500

In [1079]:
np.random.seed(0)
l_rates = (0.001, 0.0025, 0.005, 0.01, 0.05, 0.1, 0.15)
scores = []
for rate in l_rates:
    model = catboost.CatBoostClassifier(depth=depth, num_trees=tree, scale_pos_weight=scale, l2_leaf_reg=reg, learning_rate=rate,
                                       mvs_reg=mvs_reg)
    scores.append(cross_val_score(model, X_train, y_train, cv=5, scoring='f1').mean())

0:	learn: 0.6930842	total: 5.6ms	remaining: 5.6ms
1:	learn: 0.6930114	total: 10.2ms	remaining: 0us
0:	learn: 0.6930606	total: 4.69ms	remaining: 4.69ms
1:	learn: 0.6930017	total: 9.29ms	remaining: 0us
0:	learn: 0.6930890	total: 5.89ms	remaining: 5.89ms
1:	learn: 0.6930265	total: 10.8ms	remaining: 0us
0:	learn: 0.6930644	total: 10.6ms	remaining: 10.6ms
1:	learn: 0.6929942	total: 19.8ms	remaining: 0us
0:	learn: 0.6930684	total: 4.45ms	remaining: 4.45ms
1:	learn: 0.6930010	total: 9.04ms	remaining: 0us
0:	learn: 0.6929897	total: 4.3ms	remaining: 4.3ms
1:	learn: 0.6928079	total: 9.01ms	remaining: 0us
0:	learn: 0.6929309	total: 6.57ms	remaining: 6.57ms
1:	learn: 0.6927836	total: 14.3ms	remaining: 0us
0:	learn: 0.6930019	total: 5.87ms	remaining: 5.87ms
1:	learn: 0.6928456	total: 11ms	remaining: 0us
0:	learn: 0.6929403	total: 6.72ms	remaining: 6.72ms
1:	learn: 0.6927650	total: 13.1ms	remaining: 0us
0:	learn: 0.6929503	total: 4.67ms	remaining: 4.67ms
1:	learn: 0.6927819	total: 9.59ms	remaining: 

In [1080]:
scores

[0.6300161190232234,
 0.6300161190232234,
 0.6300161190232234,
 0.6300161190232234,
 0.6289038766769226,
 0.6289038766769226,
 0.6289038766769226]

In [1081]:
rate = l_rates[np.argmax(scores)]
rate

0.001

In [1082]:
np.random.seed(0)
etas = (0.001, 0.0001, 0.005, 0.1, 0.425, 0.5, 0.6, 0.55)
scores = []
for eta in etas:
    model = catboost.CatBoostClassifier(depth=depth, num_trees=tree, scale_pos_weight=scale, l2_leaf_reg=reg, eta=eta,
                                        mvs_reg=mvs_reg)
    scores.append(cross_val_score(model, X_train, y_train, cv=5, scoring='f1').mean())

0:	learn: 0.6930842	total: 5.18ms	remaining: 5.18ms
1:	learn: 0.6930114	total: 9.92ms	remaining: 0us
0:	learn: 0.6930606	total: 6.78ms	remaining: 6.78ms
1:	learn: 0.6930017	total: 13ms	remaining: 0us
0:	learn: 0.6930890	total: 5.97ms	remaining: 5.97ms
1:	learn: 0.6930265	total: 12.5ms	remaining: 0us
0:	learn: 0.6930644	total: 5.69ms	remaining: 5.69ms
1:	learn: 0.6929942	total: 13.1ms	remaining: 0us
0:	learn: 0.6930684	total: 4.57ms	remaining: 4.57ms
1:	learn: 0.6930010	total: 9.12ms	remaining: 0us
0:	learn: 0.6931409	total: 4.73ms	remaining: 4.73ms
1:	learn: 0.6931336	total: 9.35ms	remaining: 0us
0:	learn: 0.6931385	total: 4.84ms	remaining: 4.84ms
1:	learn: 0.6931326	total: 9.8ms	remaining: 0us
0:	learn: 0.6931414	total: 4.48ms	remaining: 4.48ms
1:	learn: 0.6931351	total: 9.27ms	remaining: 0us
0:	learn: 0.6931389	total: 5.2ms	remaining: 5.2ms
1:	learn: 0.6931319	total: 10.8ms	remaining: 0us
0:	learn: 0.6931393	total: 5.36ms	remaining: 5.36ms
1:	learn: 0.6931326	total: 11.3ms	remaining:

In [1083]:
scores

[0.6300161190232234,
 0.6300161190232234,
 0.6300161190232234,
 0.6289038766769226,
 0.6289038766769226,
 0.6289038766769226,
 0.6289038766769226,
 0.6289038766769226]

In [1084]:
eta=etas[np.argmax(scores)]
eta

0.001

In [1091]:
np.random.seed(0)
scales = (1.9, 2, 2.05, 2.1, 2.2, 2.3, 2.4, 2.5, 2.45, 2.35, 2.5, 2.6, 2.7, 2.8)
scores = []
for scale in scales:
    model = catboost.CatBoostClassifier(depth=depth, l2_leaf_reg=reg, num_trees=tree, eta=eta, scale_pos_weight=scale,
                                       mvs_reg=mvs_reg)
    scores.append(cross_val_score(model, X_train, y_train, cv=5, scoring='f1').mean())

0:	learn: 0.6930788	total: 4.54ms	remaining: 4.54ms
1:	learn: 0.6930135	total: 10.3ms	remaining: 0us
0:	learn: 0.6930843	total: 4.61ms	remaining: 4.61ms
1:	learn: 0.6930292	total: 9.59ms	remaining: 0us
0:	learn: 0.6930848	total: 4.36ms	remaining: 4.36ms
1:	learn: 0.6930083	total: 8.93ms	remaining: 0us
0:	learn: 0.6930799	total: 6.59ms	remaining: 6.59ms
1:	learn: 0.6930123	total: 12.4ms	remaining: 0us
0:	learn: 0.6930873	total: 4.22ms	remaining: 4.22ms
1:	learn: 0.6930144	total: 9.39ms	remaining: 0us
0:	learn: 0.6930803	total: 4.43ms	remaining: 4.43ms
1:	learn: 0.6930075	total: 9.7ms	remaining: 0us
0:	learn: 0.6930857	total: 8.61ms	remaining: 8.61ms
1:	learn: 0.6930317	total: 13.1ms	remaining: 0us
0:	learn: 0.6930862	total: 4.97ms	remaining: 4.97ms
1:	learn: 0.6930111	total: 12ms	remaining: 0us
0:	learn: 0.6930815	total: 4.4ms	remaining: 4.4ms
1:	learn: 0.6930142	total: 9.55ms	remaining: 0us
0:	learn: 0.6930683	total: 7.2ms	remaining: 7.2ms
1:	learn: 0.6929969	total: 11.6ms	remaining: 0

In [1092]:
scores

[0.6263183279181226,
 0.6261476259877248,
 0.6272554985038854,
 0.627178715572799,
 0.6274393018920172,
 0.6292647794404803,
 0.6291869089193076,
 0.6294486731495793,
 0.6291869089193076,
 0.6292647794404803,
 0.6294486731495793,
 0.6292000446475031,
 0.6289038766769226,
 0.6300161190232234]

In [1093]:
scale=scales[np.argmax(scores)]
scale

2.8

In [1088]:
np.random.seed(0)
mvs_reg = (5, 10, 15, 100,125, 150, 175)
scores = []
for mvs in mvs_reg:
    model = catboost.CatBoostClassifier(depth=depth, l2_leaf_reg=reg, num_trees=tree, eta=eta, scale_pos_weight=scale,
                                       mvs_reg=mvs)
    scores.append(cross_val_score(model, X_train, y_train, cv=5, scoring='f1').mean())

0:	learn: 0.6930842	total: 4.68ms	remaining: 4.68ms
1:	learn: 0.6930114	total: 10.1ms	remaining: 0us
0:	learn: 0.6930606	total: 5.02ms	remaining: 5.02ms
1:	learn: 0.6930017	total: 10.7ms	remaining: 0us
0:	learn: 0.6930890	total: 4.17ms	remaining: 4.17ms
1:	learn: 0.6930265	total: 8.49ms	remaining: 0us
0:	learn: 0.6930644	total: 10.6ms	remaining: 10.6ms
1:	learn: 0.6929942	total: 17.4ms	remaining: 0us
0:	learn: 0.6930684	total: 5.87ms	remaining: 5.87ms
1:	learn: 0.6930010	total: 12.2ms	remaining: 0us
0:	learn: 0.6930842	total: 8.29ms	remaining: 8.29ms
1:	learn: 0.6930114	total: 19.6ms	remaining: 0us
0:	learn: 0.6930606	total: 5.04ms	remaining: 5.04ms
1:	learn: 0.6930017	total: 12.9ms	remaining: 0us
0:	learn: 0.6930890	total: 6.47ms	remaining: 6.47ms
1:	learn: 0.6930265	total: 13ms	remaining: 0us
0:	learn: 0.6930816	total: 5.8ms	remaining: 5.8ms
1:	learn: 0.6930114	total: 10.4ms	remaining: 0us
0:	learn: 0.6930684	total: 4.38ms	remaining: 4.38ms
1:	learn: 0.6930010	total: 10.7ms	remaining

In [1089]:
scores

[0.6300161190232234,
 0.6300161190232234,
 0.6300161190232234,
 0.6289038766769226,
 0.6289038766769226,
 0.6289038766769226,
 0.6289038766769226]

In [1090]:
mvs_reg=mvs_reg[np.argmax(scores)]
mvs_reg

5

In [1069]:
model = catboost.CatBoostClassifier(depth=depth, l2_leaf_reg=reg, num_trees=tree, eta=eta, scale_pos_weight=scale,
                                   mvs_reg=mvs_reg)
model.fit(X_train, y_train)

0:	learn: 0.6930431	total: 13.2ms	remaining: 13.2ms
1:	learn: 0.6929616	total: 24.9ms	remaining: 0us


In [1005]:
cross_val_score(model, X_train, y_train, cv=5, scoring='f1').mean()

0:	learn: 0.6609299	total: 4.3ms	remaining: 47.3ms
1:	learn: 0.6349569	total: 8.7ms	remaining: 43.5ms
2:	learn: 0.6143349	total: 12.9ms	remaining: 38.8ms
3:	learn: 0.6008165	total: 17.1ms	remaining: 34.2ms
4:	learn: 0.5860511	total: 21.2ms	remaining: 29.7ms
5:	learn: 0.5766299	total: 25.3ms	remaining: 25.3ms
6:	learn: 0.5688332	total: 29.6ms	remaining: 21.2ms
7:	learn: 0.5628274	total: 34.7ms	remaining: 17.4ms
8:	learn: 0.5587800	total: 38.9ms	remaining: 13ms
9:	learn: 0.5557054	total: 45.8ms	remaining: 9.16ms
10:	learn: 0.5516548	total: 50.2ms	remaining: 4.56ms
11:	learn: 0.5492964	total: 54.2ms	remaining: 0us
0:	learn: 0.6612183	total: 4.12ms	remaining: 45.4ms
1:	learn: 0.6376418	total: 8.46ms	remaining: 42.3ms
2:	learn: 0.6207559	total: 13.2ms	remaining: 39.6ms
3:	learn: 0.6095262	total: 19.1ms	remaining: 38.3ms
4:	learn: 0.5945785	total: 26.5ms	remaining: 37ms
5:	learn: 0.5851325	total: 30.7ms	remaining: 30.7ms
6:	learn: 0.5774884	total: 34.9ms	remaining: 24.9ms
7:	learn: 0.5713877

0.6307298764461218

In [1006]:
cross_val_score(model, X_train, y_train, cv=10, scoring='f1')

0:	learn: 0.6574047	total: 21.8ms	remaining: 240ms
1:	learn: 0.6299011	total: 34.6ms	remaining: 173ms
2:	learn: 0.6104404	total: 45.3ms	remaining: 136ms
3:	learn: 0.5956394	total: 58.5ms	remaining: 117ms
4:	learn: 0.5806999	total: 73.8ms	remaining: 103ms
5:	learn: 0.5708295	total: 85.2ms	remaining: 85.2ms
6:	learn: 0.5626449	total: 99ms	remaining: 70.7ms
7:	learn: 0.5565404	total: 112ms	remaining: 56ms
8:	learn: 0.5523223	total: 125ms	remaining: 41.7ms
9:	learn: 0.5488021	total: 135ms	remaining: 27ms
10:	learn: 0.5436703	total: 146ms	remaining: 13.2ms
11:	learn: 0.5414127	total: 156ms	remaining: 0us
0:	learn: 0.6587023	total: 17.4ms	remaining: 191ms
1:	learn: 0.6325256	total: 26.8ms	remaining: 134ms
2:	learn: 0.6139545	total: 36.3ms	remaining: 109ms
3:	learn: 0.6029925	total: 46ms	remaining: 91.9ms
4:	learn: 0.5912637	total: 55.6ms	remaining: 77.8ms
5:	learn: 0.5820429	total: 65.4ms	remaining: 65.4ms
6:	learn: 0.5743902	total: 74.5ms	remaining: 53.2ms
7:	learn: 0.5695391	total: 84.4ms	

array([0.50584795, 0.65393795, 0.61103253, 0.63977747, 0.66066066,
       0.64131812, 0.56632653, 0.62644416, 0.69793103, 0.66666667])

In [1094]:
model = catboost.CatBoostClassifier(depth=5, l2_leaf_reg=22500, num_trees=13, eta=0.6, scale_pos_weight=2.6,
                                    mvs_reg=125)
model.fit(X_train, y_train)

0:	learn: 0.6405393	total: 13.3ms	remaining: 160ms
1:	learn: 0.6086893	total: 22.5ms	remaining: 124ms
2:	learn: 0.5935134	total: 32.2ms	remaining: 107ms
3:	learn: 0.5805437	total: 45.6ms	remaining: 103ms
4:	learn: 0.5671557	total: 54.4ms	remaining: 87ms
5:	learn: 0.5588101	total: 64.3ms	remaining: 75ms
6:	learn: 0.5527527	total: 74.2ms	remaining: 63.6ms
7:	learn: 0.5492084	total: 83.6ms	remaining: 52.3ms
8:	learn: 0.5460925	total: 92.4ms	remaining: 41.1ms
9:	learn: 0.5428278	total: 101ms	remaining: 30.3ms
10:	learn: 0.5402748	total: 111ms	remaining: 20.2ms
11:	learn: 0.5386533	total: 125ms	remaining: 10.4ms
12:	learn: 0.5366651	total: 136ms	remaining: 0us


In [1095]:
cross_val_score(model, X_train, y_train, cv=5, scoring='f1').mean()

0:	learn: 0.6481807	total: 7.81ms	remaining: 93.7ms
1:	learn: 0.6189057	total: 19.7ms	remaining: 108ms
2:	learn: 0.5946323	total: 27ms	remaining: 90.2ms
3:	learn: 0.5803874	total: 33.2ms	remaining: 74.7ms
4:	learn: 0.5665955	total: 41.2ms	remaining: 65.9ms
5:	learn: 0.5579110	total: 46.9ms	remaining: 54.7ms
6:	learn: 0.5505841	total: 53.3ms	remaining: 45.7ms
7:	learn: 0.5460516	total: 59.1ms	remaining: 37ms
8:	learn: 0.5429598	total: 66.8ms	remaining: 29.7ms
9:	learn: 0.5404847	total: 76.3ms	remaining: 22.9ms
10:	learn: 0.5373451	total: 82ms	remaining: 14.9ms
11:	learn: 0.5358226	total: 86.4ms	remaining: 7.2ms
12:	learn: 0.5341178	total: 91.2ms	remaining: 0us
0:	learn: 0.6487036	total: 7.49ms	remaining: 89.8ms
1:	learn: 0.6193215	total: 13.4ms	remaining: 73.8ms
2:	learn: 0.6046323	total: 17.6ms	remaining: 58.7ms
3:	learn: 0.5920866	total: 21.8ms	remaining: 49.1ms
4:	learn: 0.5769979	total: 25.9ms	remaining: 41.4ms
5:	learn: 0.5682849	total: 30.7ms	remaining: 35.8ms
6:	learn: 0.5612653	

0.6311197923218493

In [1096]:
y_test = model.predict(X_test)

In [1097]:
with open("resultBest.csv", "w", encoding='utf-8') as outfile:
    outfile.write(str("pair_id,target\n"))
    for i in range(len(y_test)):
        outfile.write(str(pair_ids[i]) + str(",") + str(y_test[i]) + str("\n"))